In [ ]:
# config.py

import torch

class Config:
    seed = 42

    # 데이터 경로
    train_path = "../database/train/train.csv"
    test_path  = "../database/test/test.csv"

    # 학습 파라미터
    batch_size = 16
    num_epochs = 20
    lr = 1e-3

    # 모델 파라미터
    embed_dim = 512
    hidden_size = 512
    num_layers = 1  # GRU 레이어 수

    device = "cuda" if torch.cuda.is_available() else "cpu"

    # 특수 토큰
    PAD_TOKEN = "[PAD]"
    UNK_TOKEN = "[UNK]"


In [32]:
# dataset.py

import torch
import torch.nn as nn
import pandas as pd
from torch.utils.data import Dataset
import numpy as np

class CharTokenizer:
    def __init__(self, vocab, pad_token, unk_token):
        self.vocab = vocab
        self.pad_token = pad_token
        self.unk_token = unk_token
        self.pad_id = vocab[pad_token]
        self.unk_id = vocab[unk_token]
        self.id2token = {v: k for k, v in vocab.items()}

    def encode(self, text):
        return [self.vocab.get(ch, self.unk_id) for ch in text]

    def decode(self, ids):
        return "".join([self.id2token.get(i, "") for i in ids if i in self.id2token])


class TokenClassifyDataset(Dataset):
    """
    난독화 해제용 (입출력 길이 무관) Dataset
    (input_str, output_str)을 (input_ids, label_ids)로 변환
    """
    def __init__(self, pairs, tokenizer):
        """
        pairs: list of (input_str, output_str)
        tokenizer: CharTokenizer
        """
        self.samples = []
        self.tokenizer = tokenizer

        for inp, outp in pairs:
            # 1) 전처리: 문장 끝의 공백 제거
            inp = inp.strip()
            outp = outp.strip()

            # 2) 토큰화
            input_ids = tokenizer.encode(inp)
            label_ids = tokenizer.encode(outp)

            # 3) 길이가 달라도 스킵하지 않고 그대로 저장
            self.samples.append((input_ids, label_ids))

    def __len__(self):
        return len(self.samples)

    def __getitem__(self, idx):
        return self.samples[idx]



def build_vocab(pairs, special_tokens):
    """
    pairs: list of (input_str, output_str)
    special_tokens: [PAD, UNK] 등
    """
    chars = set()
    for inp, outp in pairs:
        chars.update(list(inp))
        chars.update(list(outp))

    vocab = {}
    for sp in special_tokens:
        vocab[sp] = len(vocab)
    for c in sorted(list(chars)):
        if c not in vocab:
            vocab[c] = len(vocab)
    return vocab


def token_collate_fn(batch):
    """
    batch: list of (input_ids, label_ids)
    """
    import torch
    input_list, label_list = [], []
    for inp, lab in batch:
        input_list.append(torch.tensor(inp, dtype=torch.long))
        label_list.append(torch.tensor(lab, dtype=torch.long))

    # pad_sequence => (B, T)
    input_padded = nn.utils.rnn.pad_sequence(
        input_list, batch_first=True, padding_value=0
    )
    label_padded = nn.utils.rnn.pad_sequence(
        label_list, batch_first=True, padding_value=0
    )
    return input_padded, label_padded


In [18]:
# model.py

import torch
import torch.nn as nn

class BiMultiGRUModel(nn.Module):
    """
    양방향, 다층 GRU 기반
    """
    def __init__(self, vocab_size, embed_dim, hidden_size, num_layers, pad_idx=0):
        super().__init__()
        self.embedding = nn.Embedding(vocab_size, embed_dim, padding_idx=pad_idx)

        # bidirectional=True => hidden_dim * 2
        # num_layers => 몇 층 사용할지
        self.gru = nn.GRU(
            input_size=embed_dim,
            hidden_size=hidden_size,
            num_layers=num_layers,
            batch_first=True,
            bidirectional=True
        )

        # 양방향 => output_dim = hidden_size*2
        self.output_layer = nn.Linear(hidden_size * 2, vocab_size)

    def forward(self, input_ids):
        """
        input_ids: (B, T)
        return: (B, T, vocab_size)
        """
        x = self.embedding(input_ids)      # (B, T, E)
        outputs, _ = self.gru(x)          # (B, T, 2H)
        logits = self.output_layer(outputs)  # (B, T, vocab_size)
        return logits


In [22]:
# train.py

import random
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader
import pandas as pd


def set_seed(seed):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)


def train_model(model, dataloader, config):
    model.to(config.device)
    optimizer = optim.Adam(model.parameters(), lr=config.lr)
    criterion = nn.CrossEntropyLoss(ignore_index=0)  # pad=0

    for epoch in range(1, config.num_epochs + 1):
        model.train()
        total_loss = 0
        for batch in dataloader:
            input_ids, label_ids = batch
            input_ids = input_ids.to(config.device)
            label_ids = label_ids.to(config.device)

            logits = model(input_ids)  # (B, T, vocab_size)
            B, T, V = logits.size()

            loss = criterion(
                logits.view(-1, V),
                label_ids.view(-1)
            )
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            total_loss += loss.item()

        avg_loss = total_loss / len(dataloader)
        print(f"[Epoch {epoch}/{config.num_epochs}] Loss: {avg_loss:.4f}")


def predict_model(model, dataloader, tokenizer, config):
    model.eval()
    results = []
    with torch.no_grad():
        for batch in dataloader:
            input_ids, label_ids = batch
            input_ids = input_ids.to(config.device)
            
            logits = model(input_ids)  # (B, T, vocab_size)
            preds = logits.argmax(dim=-1)  # (B, T)

            # CPU로 복사
            preds_cpu = preds.cpu().numpy().tolist()
            label_cpu = label_ids.numpy().tolist()
            input_cpu = input_ids.cpu().numpy().tolist()

            # 각 샘플별 처리
            for inp_ids, lab_ids, pred_ids in zip(input_cpu, label_cpu, preds_cpu):
                # 실제 입력 길이 (PAD가 아닌 부분만 세거나, 단순히 len(inp_ids)에서 PAD 제외)
                #  여기선 간단히 inp_ids에서 0(패딩)이 나오기 전까지를 유효 길이라고 가정할 수도 있음.
                #  또는 len(inp_ids) 전체를 쓰고 뒤쪽은 PAD이니 어차피 tokenizer.decode시 무의미할 수 있음.

                # 만약 명시적으로 "입력 문자열의 실제 길이"만큼 잘라내려면:
                real_len = sum([1 for x in inp_ids if x != 0])  # 0이 아닌 토큰 개수

                # pred_ids 슬라이스: pred_ids[:real_len]
                pred_ids_sliced = pred_ids[:real_len]

                # 디코딩
                inp_str  = tokenizer.decode(inp_ids[:real_len])      # 입력도 패딩 제외
                lab_str  = tokenizer.decode(lab_ids[:real_len])      # 정답도 패딩 제외
                pred_str = tokenizer.decode(pred_ids_sliced)         # 예측도 길이 맞춰 슬라이스

                results.append((inp_str, lab_str, pred_str))
    return results



In [ ]:

if __name__ == "__main__":
    # 1) 시드 고정
    set_seed(Config.seed)

    # 2) CSV 로딩
    # train.csv에는 최소한 ["input", "output"] 컬럼이 있다고 가정
    df_train = pd.read_csv(Config.train_path)

    # (입력, 출력) 쌍 생성
    train_data = []
    for idx, row in df_train.iterrows():
        input_str = str(row["input"])
        output_str = str(row["output"])
        # 만약 길이가 다르면 TokenClassifyDataset에서 필터링될 수 있음
        train_data.append((input_str, output_str))

    # 3) Vocab & Tokenizer
    special_tokens = [Config.PAD_TOKEN, Config.UNK_TOKEN]
    vocab = build_vocab(train_data, special_tokens)
    tokenizer = CharTokenizer(vocab, Config.PAD_TOKEN, Config.UNK_TOKEN)
    print("Vocab size =", len(vocab))

    # 4) Dataset & DataLoader
    train_dataset = TokenClassifyDataset(train_data, tokenizer)
    train_loader = DataLoader(
        train_dataset,
        batch_size=Config.batch_size,
        shuffle=True,
        collate_fn=token_collate_fn
    )

    # 5) 모델 초기화
    model = BiMultiGRUModel(
        vocab_size=len(vocab),
        embed_dim=Config.embed_dim,
        hidden_size=Config.hidden_size,
        num_layers=Config.num_layers,
        pad_idx=vocab[Config.PAD_TOKEN]
    )

    # 6) 학습
    train_model(model, train_loader, Config)

    # 7) 추론 (여기서는 학습 데이터로 테스트하는 예시)
    results = predict_model(model, train_loader, tokenizer, Config)
    for inp_str, lab_str, pred_str in results:
        print(f"[입력] {inp_str} => [예측] {pred_str} (정답: {lab_str})")

In [33]:
results = predict_model(model, train_loader, tokenizer, Config)
for inp_str, lab_str, pred_str in results:
    print(f"[예측] {pred_str} (정답: {lab_str})")

[예측] 객실 넓이는 후기와 사진으로는 굉장히 좁다고 했는데, 걱정보다 그렇게 힘들진 않았습니다. 좁기는 굉장히 좁았지만, 그 넓이 안에서 목든 행동이 가능하게 구조가 잘 구성되어 있었습니다. 청결에 좀 예민한 편인데, 샤워실, 화장실, 객실, 침구, 수건, 그리고 잠옷까지 괜찮았습니다. 뷰는 정말 메인으로 광고할 만큼 좋았는데, 바다, 하늘, 그리고 광안대교가 전부 제일 예쁜 구도로 잘 보였고, 창문도 깨끗해서 밤새 바다 명 때리고 사진 많이 찍었습니다. 웰컴 드링크랑 과자, 다음날 조식까지 한 번씩 깜짝 이벤트가 있어서 기분 좋았고, 직원분들도 뭔가 일을 딱딱 잘 맞게 한다는 느낌으로 아춘 몸과 마음이 편안하고 좋았습니다. 방음 걱정했었는데 전 층 거의 다 차 있었는데도, 창문 열고 닫을 때 나는 소음이 한 번씩 있었고, 누군가가 복도에서 달려가는 소리가 났던 것 빼고는 아주 조용했습니다. 딱 한 가지 아쉬웠던 점은 창문에 방충망이 없어서 환기 시킬 때 많이 열기가 어려웠던 적이 있었습니다. 그 외에는 아주 즐거운 시간 잘 보냈습니다. (정답: 객실 넓이는 후기와 사진으로는 굉장히 좁다고 했는데, 걱정보다 그렇게 힘들진 않았습니다. 좁기는 굉장히 좁았지만, 그 넓이 안에서 모든 행동이 가능하게 구조가 잘 구성되어 있었습니다. 청결에 좀 예민한 편인데, 샤워실, 화장실, 객실, 침구, 수건, 그리고 잠옷까지 괜찮았습니다. 뷰는 정말 메인으로 광고할 만큼 좋았는데, 바다, 하늘, 그리고 광안대교가 전부 제일 예쁜 구도로 잘 보였고, 창문도 깨끗해서 밤새 바다 멍 때리고 사진 많이 찍었습니다. 웰컴 드링크랑 과자, 다음날 조식까지 한 번씩 깜짝 이벤트가 있어서 기분 좋았고, 직원분들도 뭔가 일을 딱딱 잘 맞게 한다는 느낌으로 아주 몸과 마음이 편안하고 좋았습니다. 방음 걱정했었는데 전 층 거의 다 차 있었는데도, 창문 열고 닫을 때 나는 소음이 한 번씩 있었고, 누군가가 복도에서 달려가는 소리가 났던 것 빼고는 아주 조용했습니다. 딱 한 가지 아쉬웠던 점은 창문

In [34]:
# 4) Dataset & DataLoader
df_test = pd.read_csv(Config.test_path)
df_test["output"] = ""

# (입력, 출력) 쌍 생성
test_data = []
for idx, row in df_test.iterrows():
    input_str = str(row["input"])
    output_str = str(row["output"])
    # 만약 길이가 다르면 TokenClassifyDataset에서 필터링될 수 있음
    test_data.append((input_str, output_str))

test_dataset = TokenClassifyDataset(test_data, tokenizer)
test_loader = DataLoader(
    test_dataset,
    batch_size=Config.batch_size,
    shuffle=False,
    collate_fn=token_collate_fn
)
preds = predict_model(model, test_loader, tokenizer, Config)

In [37]:
sub = []
for input, output, pred in preds:
    sub.append(pred)
df_sub = pd.read_csv('../database/submission/sample_submission.csv')
df_sub["output"] = sub
df_sub.to_csv('../database/submission/gru_submission.csv', index = False)